In [1]:
import folium
import pandas as pd
import json
import os
import jenkspy

# Employee Dataframe

In [2]:
# Load the spreadsheet
file_path = 'allactive.xlsx'

# Load the SortedSummary sheet into a DataFrame
df_sorted_summary = pd.read_excel(file_path, sheet_name='RidersSummary')

# Extract the ID and TotalRider columns
employee_counts = df_sorted_summary[['ID', 'TotalRiders']]

# Same as above for each barangay
alabang_counts = df_sorted_summary[['ID', 'Alabang']]
binan_counts = df_sorted_summary[['ID', 'Bi√±an']]
balibago_counts = df_sorted_summary[['ID', 'Balibago']]
cabuyao_counts = df_sorted_summary[['ID', 'Cabuyao']]
calamba_counts = df_sorted_summary[['ID', 'Calamba']]

# Function to prepend 'PH' or 'PH0' based on the length of the ID
def prepend_ph(id_value):
    id_str = str(id_value)
    if len(id_str) == 9:
        return 'PH' + id_str
    elif len(id_str) == 8:
        return 'PH0' + id_str
    else:
        return id_str

# Apply the function to the ID column
employee_counts.loc[:, 'ID'] = employee_counts['ID'].apply(prepend_ph)
alabang_counts.loc[:, 'ID'] = alabang_counts['ID'].apply(prepend_ph)
binan_counts.loc[:, 'ID'] = binan_counts['ID'].apply(prepend_ph)
balibago_counts.loc[:, 'ID'] = balibago_counts['ID'].apply(prepend_ph)
cabuyao_counts.loc[:, 'ID'] = cabuyao_counts['ID'].apply(prepend_ph)
calamba_counts.loc[:, 'ID'] = calamba_counts['ID'].apply(prepend_ph)

# Display the first few rows of the modified DataFrame
print(employee_counts.head())

            ID  TotalRiders
0  PH137603004            4
1  PH137607021            1
2  PH137603001            8
3  PH137603006            4
4  PH137604007            3


In [3]:
# Initialization code
jsonfolder_path = ['/Users/jerritor2/Desktop/EMS_Data/Bus_Analysis/philippines-json-maps/2023/geojson/municities/hires',
                  '/Users/jerritor2/Desktop/EMS_Data/Bus_Analysis/philippines-json-maps/2019/geojson/barangays/hires']

m = folium.Map()

def generateMapLocation(mapfocusindex):
    global m
    if mapfocusindex == 0:
        m = folium.Map(location=[12.616870715056407, 122.34833708101706], zoom_start=5.5)
    elif mapfocusindex == 1:
        m = folium.Map(location=[14.468224838723954, 121.04553358573668], zoom_start=10)
    else:
        m = folium.Map(location=[14.274281440588128, 121.05943840821561], zoom_start=11)

def generateMapLevel(fpathindex):
    geojson_data = {'type': 'FeatureCollection', 'features': []}
    geojson_dict = {}
    for filename in os.listdir(jsonfolder_path[fpathindex]):
        if filename.endswith('.json'):
            file_path = os.path.join(jsonfolder_path[fpathindex], filename)
            with open(file_path, 'r') as file:
                data = json.load(file)
                for feature in data['features']:
                    pcode = feature['properties']['ADM4_PCODE']
                    geojson_dict[pcode] = feature
                    geojson_data['features'].append(feature)
    return geojson_dict

def generateMap(focusindex, pathindex):
    generateMapLocation(focusindex)
    geojson_dict = generateMapLevel(pathindex)
    return geojson_dict

geojson_dict = generateMap(2, 1)

def add_choropleth_layer(data, column_name, layer_name, legend_name, fill_color, show=True):
    data.loc[:, 'ID'] = data['ID'].astype(str)
    filtered_features = [geojson_dict[code] for code in data['ID'] if code in geojson_dict]
    for feature in filtered_features:
        pcode = feature['properties']['ADM4_PCODE']
        feature['properties'][column_name] = int(data.loc[data['ID'] == pcode, column_name].values[0])
    filtered_geojson_data = {'type': 'FeatureCollection', 'features': filtered_features}
    
    # Determine the number of unique values in the column
    num_unique_values = data[column_name].nunique()
    
    # Set the number of bins for Jenks breaks (must be between 1 and the number of unique values)
    num_bins = min(num_unique_values, 5)
    
    folium.Choropleth(
        geo_data=filtered_geojson_data,
        name=layer_name,
        data=data,
        columns=['ID', column_name],
        key_on='feature.properties.ADM4_PCODE',
        nan_fill_color='blue',
        fill_color=fill_color,
        highlight=True,
        bins=num_bins if num_bins > 1 else None,  # Use bins only if more than one unique value
        use_jenks=num_bins > 1,  # Use Jenks breaks only if more than one unique value
        legend_name=legend_name,
        show=show
    ).add_to(m)
    return filtered_geojson_data

# Adding layers for each route with different colors and starting off disabled (except employee count)
employee_geojson = add_choropleth_layer(employee_counts, 'TotalRiders', 'Employee Count', 'Employee Count', 'OrRd', show=True)
alabang_geojson = add_choropleth_layer(alabang_counts, 'Alabang', 'Alabang Route', 'Alabang Riders', 'BuGn', show=False)
binan_geojson = add_choropleth_layer(binan_counts, 'Bi√±an', 'Bi√±an Route', 'Biñan Riders', 'BuPu', show=False)
balibago_geojson = add_choropleth_layer(balibago_counts, 'Balibago', 'Balibago Route', 'Balibago Riders', 'GnBu', show=False)
cabuyao_geojson = add_choropleth_layer(cabuyao_counts, 'Cabuyao', 'Cabuyao Route', 'Cabuyao Riders', 'PuBu', show=False)
calamba_geojson = add_choropleth_layer(calamba_counts, 'Calamba', 'Calamba Route', 'Calamba Riders', 'PuBuGn', show=False)

# Merge all features into one GeoJSON for tooltips
all_features = employee_geojson['features']
for geojson in [alabang_geojson, binan_geojson, balibago_geojson, cabuyao_geojson, calamba_geojson]:
    for feature in geojson['features']:
        for all_feature in all_features:
            if all_feature['properties']['ADM4_PCODE'] == feature['properties']['ADM4_PCODE']:
                all_feature['properties'].update(feature['properties'])

# Create a merged GeoJSON structure
merged_geojson_data = {'type': 'FeatureCollection', 'features': all_features}

# Add tooltips to the GeoJSON layer
folium.GeoJson(
    merged_geojson_data,
    name='Tooltip Layer',  # Change the name to avoid confusion
    style_function=lambda x: {
        'fillColor': 'transparent',
        'color': 'black',
        'weight': 0.5,
        'opacity': 0.5
    },
    tooltip=folium.GeoJsonTooltip(
        fields=['ADM1_EN', 'ADM2_EN', 'ADM3_EN', 'ADM4_EN', 'TotalRiders', 'Alabang', 'Bi√±an', 'Balibago', 'Cabuyao', 'Calamba'],
        aliases=['Region: ', 'Province: ', 'Municipality: ', 'Barangay: ', 'Total Riders: ', 'Alabang: ', 'Biñan: ', 'Balibago: ', 'Cabuyao: ', 'Calamba: '],
        fill_opacity=0,
        line_opacity=0,
        localize=True
    )
).add_to(m)

In [4]:
# Add layer control
folium.LayerControl().add_to(m)

# Save the map to an HTML file
m.save('riders.html')

In [5]:
m

# Initialization code
jsonfolder_path = ['/Users/jerritor2/Desktop/EMS_Data/Bus_Analysis/philippines-json-maps/2023/geojson/municities/hires',
                  '/Users/jerritor2/Desktop/EMS_Data/Bus_Analysis/philippines-json-maps/2019/geojson/barangays/hires']

m = folium.Map()

def generateMapLocation(mapfocusindex):
    global m
    
    if mapfocusindex == 0: # all ph
        m = folium.Map(location=[12.616870715056407, 122.34833708101706], zoom_start=5.5)
        print("Setting focus to all of Philippines")
    elif mapfocusindex == 1: # calabarzon + metro manila
        m = folium.Map(location=[14.468224838723954, 121.04553358573668], zoom_start=10)
        print("Setting focus to Calabarzon + Metro Manila")
    else: # calabarzon centered on calamba
        m = folium.Map(location=[14.274281440588128, 121.05943840821561], zoom_start=11)
        print("Setting focus to Calabarzon")

def generateMapLevel(fpathindex):
    if fpathindex == 0:
        print("Setting borders to 2023 Municipalities")
    else:
        print("Setting borders to 2019 Barangays")
    
    # Read and store GeoJSON data
    geojson_data = {'type': 'FeatureCollection', 'features': []}
    geojson_dict = {}
    for filename in os.listdir(jsonfolder_path[fpathindex]):
        if filename.endswith('.json'):
            file_path = os.path.join(jsonfolder_path[fpathindex], filename)
            with open(file_path, 'r') as file:
                data = json.load(file)
                for feature in data['features']:
                    pcode = feature['properties']['ADM4_PCODE']
                    geojson_dict[pcode] = feature
                    geojson_data['features'].append(feature)
    
    print("GeoJSON data loaded.")
    return geojson_dict

def generateMap(focusindex, pathindex):
    generateMapLocation(focusindex)
    geojson_dict = generateMapLevel(pathindex)
    return geojson_dict

# Load the GeoJSON data for barangays
geojson_dict = generateMap(2, 1)

# Ensure ID column is string
employee_counts.loc[:, 'ID'] = employee_counts['ID'].astype(str)

# Filter GeoJSON features to include only those with matching IDs in the employee_counts DataFrame
filtered_features = [geojson_dict[code] for code in employee_counts['ID'] if code in geojson_dict]

# Add the count to the properties of each feature, converting it to a regular Python int
for feature in filtered_features:
    pcode = feature['properties']['ADM4_PCODE']
    feature['properties']['Count'] = int(employee_counts.loc[employee_counts['ID'] == pcode, 'Count'].values[0])

#all_features = [geojson_dict[code] for code in employee_counts['ID']]

# Create a new GeoJSON structure with filtered features
filtered_geojson_data = {'type': 'FeatureCollection', 'features': filtered_features}

############
# Create a choropleth map using Folium
folium.Choropleth(
    geo_data=filtered_geojson_data,
    name='choropleth',
    data=employee_counts,
    columns=['ID', 'Count'],
    key_on='feature.properties.ADM4_PCODE',
    nan_fill_color='blue',
    #nan_fill_opacity=0.5,
    fill_color='OrRd',
    #fill_opacity=0.7,
    #line_opacity=0.2,
    highlight=True,
    use_jenks=True,
    #bins=[1,2,3,4,5,6,7,8,9,10,11,12,13,15,16,17,18,19,20,25,27,36,41,55],
    legend_name='Employee Count'
).add_to(m)


# Add tooltips to the GeoJSON layer
folium.GeoJson(
    filtered_geojson_data,
    #all_features,
    name='barangay_overlays',
    style_function=lambda x: {
        'fillColor': 'transparent',
        'color': 'black',
        'weight': 0.5,
        'opacity': 0.5
    },
    tooltip=folium.GeoJsonTooltip(
        fields=['ADM1_EN','ADM2_EN','ADM3_EN','ADM4_EN', 'Count'],
        aliases=['Region: ','Province: ','Municipality: ','Barangay: ', 'Employee Count: '],
        fill_opacity=0,
        line_opacity=0,
        localize=True
    )
).add_to(m)

# Add layer control
folium.LayerControl().add_to(m)

# Save the map to an HTML file
m.save('allactive.html')

In [ ]:
# Display the map in Jupyter Notebook (if running in such an environment)
m